In [1]:
from data import generate_batches
from data import prepare_data
from data import data_to_index
from data import DEP_LABELS

from model.graph import Sintactic_GCN
from model.encoder import Encoder
from model.decoder import Decoder_luong

from utils import time_since

import torch
import torch.nn as nn
from torch.nn import functional
from torch.autograd import Variable
from torch import optim
import torch.nn.functional as F

from stanfordcorenlp import StanfordCoreNLP 

import numpy as np
import time

%load_ext autoreload
%autoreload 2

In [2]:
USE_CUDA = True
MAX_LENGTH = 100

SPLIT_TRAIN = 0.7
SPLIT_VALID = 0.15
# The rest is for test

# Reading the data

Prepare vocabulary and pairs for the data

In [4]:
en_vec, spa_vec, pairs = prepare_data('en', 'spa', )

Reading lines...
Read 118964 sentence pairs
Filtered to 118316 pairs
Creating vocab...
Indexed 15720 words in input language, 28199 words in output


Splitting pairs into test, val and test

In [5]:
pairs_train = pairs[:int(len(pairs) * SPLIT_TRAIN)]
pairs_valid = pairs[int(len(pairs) * SPLIT_TRAIN):int(len(pairs) * (SPLIT_TRAIN + SPLIT_VALID))]
pairs_test = pairs[int(len(pairs) * (SPLIT_TRAIN + SPLIT_VALID)):]

In [6]:
len(pairs_train), len(pairs_valid), len(pairs_test)

(82821, 17747, 17748)

Get the adjacency matrix for the pairs

In [7]:
nlp = StanfordCoreNLP(r'/home/krivas/stanford-corenlp-full-2018-02-27/')

In [8]:
from tqdm import tqdm
def get_adjacency_matrix(pairs):
    arr_dep = []
    for pair in tqdm(pairs):
        arr_dep.append(nlp.dependency_parse(pair[0]))
    return np.array(arr_dep)

In [10]:
arr_dep_train = get_adjacency_matrix(pairs_train)
arr_dep_valid = get_adjacency_matrix(pairs_valid)
arr_dep_test = get_adjacency_matrix(pairs_test)

100%|██████████| 17748/17748 [04:47<00:00, 61.74it/s]


Converting words to index in pairs

In [13]:
pairs_train = data_to_index(pairs_train, en_vec, spa_vec)
pairs_valid = data_to_index(pairs_valid, en_vec, spa_vec)
pairs_test = data_to_index(pairs_test, en_vec, spa_vec)

# Training

In [15]:
def pass_batch_luong(input_lang, output_lang, encoder, decoder, gcn1, gcn2, batch_size, input_batches, target_batches, tf_ratio, train=True, adj_arc_in=None, adj_arc_out=None, adj_lab_in=None, adj_lab_out=None, mask_in=None, mask_out=None, mask_loop=None, USE_CUDA=False):
        
    cell = encoder.init_cell(batch_size)
    hidden = encoder.init_hidden(batch_size)

    encoder_outputs, encoder_hidden = encoder(input_batches, hidden, cell)
    decoder_input = Variable(torch.LongTensor([input_lang.vocab.stoi["<sos>"]] * batch_size))
    
    if gcn1:
        encoder_outputs = gcn1(encoder_outputs,
                             adj_arc_in, adj_arc_out,
                             adj_lab_in, adj_lab_out,
                             mask_in, mask_out,  
                             mask_loop)
    if gcn2:     
        encoder_outputs = gcn2(encoder_outputs,
                             adj_arc_in, adj_arc_out,
                             adj_lab_in, adj_lab_out,
                             mask_in, mask_out,  
                             mask_loop)
    
    decoder_hidden = encoder_hidden
    decoder_cell = encoder_cell
    decoder_context = Variable(torch.zeros(batch_size, decoder.hidden_size)) 
    
    all_decoder_outputs = Variable(torch.zeros(target_batches.data.size()[0], batch_size, len(output_lang.vocab.itos)))

    if USE_CUDA:
        all_decoder_outputs = all_decoder_outputs.cuda()
        decoder_input = decoder_input.cuda()
        decoder_context = decoder_context.cuda()
    
    if train:
        use_teacher_forcing = np.random.random() < tf_ratio
    else:
        use_teacher_forcing = False
    
    if use_teacher_forcing:        
        # Use targets as inputs
        for di in range(target_batches.shape[0]):
            decoder_output, decoder_context, decoder_hidden, decoder_attention = decoder(
                decoder_input.unsqueeze(0), decoder_context, decoder_hidden, encoder_outputs)
            
            all_decoder_outputs[di] = decoder_output
            decoder_input = target_batches[di]
    else:        
        # Use decoder output as inputs
        for di in range(target_batches.shape[0]):            
            decoder_output, decoder_context, decoder_hidden, decoder_attention = decoder(
                decoder_input.unsqueeze(0), decoder_context, decoder_hidden, encoder_outputs) 
            
            all_decoder_outputs[di] = decoder_output
            
            # Greedy approach, take the word with highest probability
            topv, topi = decoder_output.data.topk(1)            
            decoder_input = Variable(torch.LongTensor(topi.cpu()).squeeze())
            if USE_CUDA: decoder_input = decoder_input.cuda()
        
    del decoder_output
    del decoder_hidden
        
    return all_decoder_outputs, target_batches

def train_luong(input_lang, output_lang, input_batches, target_batches, batch_size, encoder, decoder, gcn1, gcn2, encoder_optimizer, decoder_optimizer, gcn1_optimizer, gcn2_optimizer, criterion, tf_ratio, max_length, clip=None, train=True, adj_arc_in=None, adj_arc_out=None, adj_lab_in=None, adj_lab_out=None, mask_in=None, mask_out=None, mask_loop=None, USE_CUDA=False):
    
    # Zero gradients of both optimizers
    if train:
        encoder_optimizer.zero_grad()
        decoder_optimizer.zero_grad()

    loss = 0 # Added onto for each word

    all_decoder_outputs, target_batches = pass_batch_luong(input_lang, output_lang, encoder, decoder, gcn1, gcn2, batch_size, input_batches, target_batches, tf_ratio, train, adj_arc_in, adj_arc_out, adj_lab_in, adj_lab_out, mask_in, mask_out, mask_loop, USE_CUDA)
    
    # Loss calculation and backpropagation
    loss = criterion(all_decoder_outputs.view(-1, decoder.output_size), target.view(-1))
    
    if train:
        loss.backward()
        torch.nn.utils.clip_grad_norm_(encoder.parameters(), clip)
        torch.nn.utils.clip_grad_norm_(decoder.parameters(), clip)
        encoder_optimizer.step()
        decoder_optimizer.step()
    
    del all_decoder_outputs
    del target_batches
    
    return loss.item()

# Model

In [16]:
# Configure models
hidden_size_rnn = 512
hidden_size_graph = 512
emb_size=300
n_layers = 2
dropout = 0.1
batch_size = 50

# Configure training/optimization
clip = 10.0
learning_rate_graph = 0.0002
n_epochs = 50
print_every = 10
validate_loss_every = 50
validate_acc_every = 2 * validate_loss_every
tf_ratio = 0.5

In [38]:
# Initialize models
encoder = Encoder(len(en_vec.vocab.itos), hidden_size_rnn, emb_size, n_layers=n_layers, dropout=dropout, USE_CUDA=USE_CUDA)
decoder = Decoder_luong('general', hidden_size_graph, len(spa_vec.vocab.itos), 300, n_layers=2 * n_layers, dropout=dropout, USE_CUDA=USE_CUDA)
gcn1 = Sintactic_GCN(hidden_size_rnn, hidden_size_graph, num_labels=len(DEP_LABELS))

# Initialize optimizers and criterion
encoder_optimizer = optim.Adam(encoder.parameters())
decoder_optimizer = optim.Adam(decoder.parameters())
gcn1_optimizer = optim.Adam(gcn1.parameters(), learning_rate_graph)

criterion = nn.NLLLoss()

# Move models to GPU
if USE_CUDA:
    encoder = encoder.cuda()
    decoder = decoder.cuda()
    gcn1 = gcn1.cuda()
    
# Keep track of time elapsed and running averages
start = time.time()
train_losses = []
validation_losses = []
validation_acc = []

print_loss_total = 0 # Reset every print_every
plot_loss_total = 0 # Reset every plot_every

In [ ]:
for epoch in range(n_epochs): 
    # Shuffle data
    id_aux = np.random.permutation(np.arange(len(pairs_train)))
    pairs_train = pairs_train[id_aux]
    arr_dep_train = arr_dep_train[id_aux]
    
    # Get the batches for this epoch
    input_batches, target_batches = generate_batches(en_vec, spa_vec, batch_size, pairs_train, return_dep_tree=True, arr_dep=arr_dep_train, max_degree=6, USE_CUDA=USE_CUDA)
    print_loss_total = 0
    for batch_ix, input_batch, target_var in enumerate(zip(input_batches, target_batches)):
    
        encoder.train()
        decoder.train()
        gcn1.train()
    
        [input_var, adj_arc_in, adj_arc_out, adj_lab_in, adj_lab_out, mask_in, mask_out, mask_loop] = input_batch
        # Run the train function
        loss = train_luong(en_vec, spa_vec,
                    input_var, target_var, batch_size, 
                    encoder, decoder, gcn1, None, encoder_optimizer, decoder_optimizer, gcn1_optimizer, None, 
                    criterion, tf_ratio, MAX_LENGTH,
                    clip, True, adj_arc_in, adj_arc_out, adj_lab_in, adj_lab_out, mask_in, mask_out, mask_loop, USE_CUDA)
            
        torch.cuda.empty_cache()

        # Keep track of loss
        print_loss_total += loss
        plot_loss_total += loss

        if batch_ix == 0: continue

        if batch_ix % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print_summary = '%s (%d %d%%) %.4f' % (time_since(start, epoch / n_epochs), epoch, epoch / n_epochs * 100, print_loss_avg)
            train_losses.append(loss)

            print(f'{time_since(start, epoch / n_epochs)} ({epoch} {epoch / n_epochs * 100:.2f}%) train_loss: {print_loss_avg:.4f}', end=' ')
    
    input_batches, target_batches = generate_batches(input_vec, output_vec, batch_size, pairs_valid, return_dep_tree=True, arr_dep=arr_dep_train, max_degree=6, USE_CUDA=USE_CUDA)
    print_loss_total = 0
    for input_batch, target_var in zip(input_batches, target_batches):
    
        encoder.eval()
        decoder.eval()
        gcn1.eval()
    
        [input_var, adj_arc_in, adj_arc_out, adj_lab_in, adj_lab_out, mask_in, mask_out, mask_loop] = input_batch
        # Run the train function
        loss = train_luong(input_lang, output_lang,
                    input_var, target_var, batch_size, 
                    encoder, decoder, gcn1, None, encoder_optimizer, decoder_optimizer, gcn1_optimizer, None, 
                    criterion, tf_ratio, MAX_LENGTH,
                    clip, True, adj_arc_in, adj_arc_out, adj_lab_in, adj_lab_out, mask_in, mask_out, mask_loop, USE_CUDA)
        
        print_loss_total += loss
    val_loss = print_loss_total / len(input_batches)
    validation_losses.append(val_loss)
    print(f'val_loss: {eval_loss:.4f} - bleu: {bleu}', end=' ')



In [75]:
generate_batches(en_vec, spa_vec, 10, pairs_train, return_dep_tree=False)


0
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390
400
410
420
430
440
450
460
470
480
490
500
510
520
530
540
550
560
570
580
590
600
610
620
630
640
650
660
670
680
690
700
710
720
730
740
750
760
770
780
790
800
810
820
830
840
850
860
870
880
890
900
910
920
930
940
950
960
970
980
990
1000
1010
1020
1030
1040
1050
1060
1070
1080
1090
1100
1110
1120
1130
1140
1150
1160
1170
1180
1190
1200
1210
1220
1230
1240
1250
1260
1270
1280
1290
1300
1310
1320
1330
1340
1350
1360
1370
1380
1390
1400
1410
1420
1430
1440
1450
1460
1470
1480
1490
1500
1510
1520
1530
1540
1550
1560
1570
1580
1590
1600
1610
1620
1630
1640
1650
1660
1670
1680
1690
1700
1710
1720
1730
1740
1750
1760
1770
1780
1790
1800
1810
1820
1830
1840
1850
1860
1870
1880
1890
1900
1910
1920
1930
1940
1950
1960
1970
1980
1990
2000
2010
2020
2030
2040
2050
2060
2070
2080
2090
2100
2110
2120
2130
2140
2150
2160
2170
2180
2190
2200
2210
2

([[tensor([[  729,   111,    25,    55,   128,     5,     5,     6,     9,    28],
           [   64,     8,  3570,     8,   101,  4906,   143,    26,    12,    12],
           [  184,  3252,   492,   148,   157,    12,  3923,    36,    37,    21],
           [   18,     5,     7,     5,    24, 14979,    15,     7,    53,  2466],
           [    4,   982,   217,   646,    46,     4,  4236,    45,   354,    24],
           [    3,    10,     4,    11,     4,     3,     4,   116,    53,    11],
           [    1,   172,     3,     3,     3,     1,     3,     7,     6,     3],
           [    1,    11,     1,     1,     1,     1,     1,   993,    98,     1],
           [    1,     3,     1,     1,     1,     1,     1,     4,     4,     1],
           [    1,     1,     1,     1,     1,     1,     1,     3,     3,     1]]),
   None,
   None,
   None,
   None,
   None,
   None,
   None],
  [tensor([[  26,    6,    6,   25,    9,    9,   83,    6,  191,   52],
           [ 135,   26,  153,  

In [73]:
len(pairs_train)

82821

In [68]:
    for pos in range(0, len(pairs_train), 10):
        # Avoiding out of array
        print(len(pairs))
        print(pos)
        print(batch_size)
        cant = min(10, len(pairs_train) - pos - 1)
        
        input_seqs = pairs_train[pos:cant+pos, 0].tolist()
        target_seqs = pairs_train[pos:cant+pos, 1].tolist()
        print(input_seqs)

118316
0
50
[[729, 64, 184, 18, 4, 3, 1, 1, 1, 1], [111, 8, 3252, 5, 982, 10, 172, 11, 3, 1], [25, 3570, 492, 7, 217, 4, 3, 1, 1, 1], [55, 8, 148, 5, 646, 11, 3, 1, 1, 1], [128, 101, 157, 24, 46, 4, 3, 1, 1, 1], [5, 4906, 12, 14979, 4, 3, 1, 1, 1, 1], [5, 143, 3923, 15, 4236, 4, 3, 1, 1, 1], [6, 26, 36, 7, 45, 116, 7, 993, 4, 3], [9, 12, 37, 53, 354, 53, 6, 98, 4, 3], [28, 12, 21, 2466, 24, 11, 3, 1, 1, 1]]
118316
10
50
[[26, 135, 245, 23, 4, 3, 1, 1, 1, 1], [6, 26, 36, 7, 337, 114, 4, 3, 1, 1], [6, 153, 32, 633, 4, 3, 1, 1, 1, 1], [25, 177, 23, 1319, 5, 603, 4, 3, 1, 1], [9, 261, 21, 339, 4, 3, 1, 1, 1, 1], [9, 47, 70, 7126, 2747, 4, 3, 1, 1, 1], [83, 37, 476, 4, 3, 1, 1, 1, 1, 1], [6, 17, 33, 5, 399, 4, 3, 1, 1, 1], [191, 31, 621, 114, 58, 110, 4, 3, 1, 1], [52, 56, 254, 7, 202, 16, 151, 4, 3, 1]]
118316
20
50
[[142, 37, 717, 4, 3, 1, 1, 1, 1, 1], [199, 18, 342, 2557, 82, 4, 3, 1, 1, 1], [190, 6, 216, 8, 10, 396, 11, 3, 1, 1], [214, 564, 27, 727, 4, 3, 1, 1, 1, 1], [199, 21, 4, 3, 1,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.
